In [99]:
import re
import requests
import os
from nltk.tokenize import RegexpTokenizer 
from nltk.tokenize import sent_tokenize
from nltk.probability import *
# import collections
import pandas as pd

In [2]:
!pip install pdfminer.six

In [3]:
! pdf2txt.py -o Group148.txt Group148.pdf

First, let's read the new text file into python.

In [4]:
pdfTxtFile = './Group148.txt'
pdf_txt = open(pdfTxtFile, 'r')
# loop over all the lines
for line in pdf_txt:
    # repr() is a built-in Python fuction that returns a string containing a printable representation of an object.
    print (repr(line))

'filename\n'
'\n'
'url\n'
'\n'
'PP3197.pdf https://drive.google.com/uc?export=download&id=1z9rts_mqD0rk1cztTomCZEmYu2Xv10iv\n'
'PP3200.pdf https://drive.google.com/uc?export=download&id=1WHdSDs92fR7bUTy0nV3SWxwP9DCQcnkJ\n'
'PP3210.pdf https://drive.google.com/uc?export=download&id=1wdymTR6vczfMLbzhaqtQs_OH9yRgk42k\n'
'PP3213.pdf https://drive.google.com/uc?export=download&id=1YibLIdUQxCnuN_zroe-iAG9FgWDbZ-HA\n'
'PP3292.pdf https://drive.google.com/uc?export=download&id=1mNx32AK8ofiOe3RhTKouelHpN8xn9n0K\n'
'PP3348.pdf https://drive.google.com/uc?export=download&id=1eBChiTzSY239TS5pJVYoZ1r4AF51EHnE\n'
'PP3382.pdf https://drive.google.com/uc?export=download&id=1L-6YTB6fPkS-0JVFvzxfH9f0PSxnnpmI\n'
'PP3399.pdf https://drive.google.com/uc?export=download&id=1bLBmPNxzLOpja_t4UJLq1Pi75gc0EkZ1\n'
'PP3416.pdf https://drive.google.com/uc?export=download&id=1POGclPS_-XkOBcNeA1HXWB_flRIpUJ6T\n'
'PP3425.pdf https://drive.google.com/uc?export=download&id=1mY-1DjPyGnJn0NmZ-JcHokBgVcUzT3Ed\n'
'PP3452.p

The above code read the text file line-by-line and printed each line. You should notice that we have converted each line into a printable representation of a string object using Python's build-in function, repr(), as it will help us discover some patterns that can be used to extract those data tables.

In [5]:
pdfTxtFile = './Group148.txt'
with open(pdfTxtFile, 'r') as f:
    pdf_txt=f.readlines()
file_name = []
file_url = []
reg1 = re.compile(r'(PP\d{4}).pdf')
reg2 = re.compile(r'(https://[\s\S]+?)\n')
for line in pdf_txt:
    if reg1.search(line):
        file_name.append((reg1.search(line).group(1)))
for line in pdf_txt:
    if reg2.search(line):
        file_url.append((reg2.search(line).group(1)))
Dict=dict(zip(file_name,file_url))

In [6]:
def downloadFile(url, fileName):
    with open(fileName+'.pdf', "wb") as file:
        response = requests.get(url)
        file.write(response.content)

In [38]:
for key, value in Dict.items():
    downloadFile(value, key)

In [39]:
for key in Dict.keys():
    os.system("pdf2txt.py -o %s %s" % (key+'.txt', key+'.pdf'))

In [203]:
# # Task 1
# # Preparing data
# rawdict={}
# filetxt=[key+'.txt' for key in Dict.keys()]
# for file in filetxt:
#     rawdoc=''
#     with open(file,'r',encoding='utf-8') as f:
#         for line in f:
#             rawdoc += line.strip() + ' '
# #         rawdata=re.search(r'Paper Body(.*?)2 References',rawdoc).group(1)
# #         rawdict[file[:-4]]=rawdata 
# # rawdict
# # rawdata
# rawdoc

In [6]:
filenames = [key+'.txt' for key in Dict.keys()]
files ={}
for each in filenames:
#     rawdoc=''
    with open(each,'r', encoding="utf8") as f:
#         for line in f:
#             rawdoc += line.strip() + ' '
        if each in files:
            continue
        files[each] = f.read().strip()          
files

{'PP3197.txt': 'Online Linear Regression and Its Application to\n\nModel-Based Reinforcement Learning\n\nAuthored by:\n\nMichael L. Littman\nAlexander L. Strehl\n\nAbstract\n\nWe provide a provably eﬃcient algorithm for learning Markov Decision\nProcesses (MDPs) with continuous state and action spaces in the online\nsetting. Speciﬁcally, we take a model-based approach and show that a\nspecial type of online linear regression allows us to learn MDPs with (pos-\nsibly kernalized) linearly parameterized dynamics. This result builds on\nKearns and Singh’s work that provides a provably eﬃcient algorithm for\nﬁnite state MDPs. Our approach is not restricted to the linear setting,\nand is applicable to other classes of continuous MDPs.\n\n1 Paper Body\n\nCurrent reinforcement-learning (RL) techniques hold great promise for creating\na general type of artiﬁcial intelligence (AI), speciﬁcally autonomous (software)\nagents that learn diﬃcult tasks with limited feedback (Sutton & Barto, 1998).\nA

In [7]:
with open('stopwords_en.txt','r') as f:
    stop_word = f.read().splitlines()  

In [114]:
def clean(line):
    whole = [each.strip() for each in line]
    whole = ''.join(whole)
    each = re.sub(r'\n',' ',whole)
    each = re.sub(r'\-\s','',each)
    return each

In [115]:
def token(line):
    tokenizer = RegexpTokenizer(r'[A-Za-z]\w+(?:[-?]\w+)?')
    each = tokenizer.tokenize(line)     
    return each

In [116]:
def sent_token(line):
    whole = sent_tokenize(line)
    whole = [each[0].lower() + each[1:] for each in whole]
    whole = ''.join(whole)
    return whole

In [117]:
#create list for title, author and abstract respectively
title_list = []
author_list = []
abstract_list = []
reg3 = re.compile(r'Authored\sby:([\s\S]*?)Abstract')
reg4 = re.compile(r'([\s\S]+?)Authored\sby')
reg5 = re.compile(r'Abstract([\s\S]+?)1\sPaper\sBody')
tokenizer = RegexpTokenizer(r'[A-Za-z]\w+(?:[-?]\w+)?')
for key, value in files.items():
    if reg4.search(value):
        title_list.append(reg4.search(value).group(1))
    if reg3.search(value):
        author_list.append(reg3.search(value).group(1))
    if reg5.search(value):
        abstract_list.append(reg5.search(value).group(1))   
author_list = ''.join(author_list)
author_list = author_list.splitlines()
author_list = [each for each in author_list if each] 

title_list = clean(title_list)
title_list = token(title_list)
title_list = [token.lower() for token in title_list]
title_list = [w for w in title_list if w not in stop_word]

abstract_list = clean(abstract_list)
abstract_list = sent_token(abstract_list)
abstract_list = token(abstract_list)
abstract_list = [w for w in abstract_list if w not in stop_word]

In [219]:
#create list for title, author and abstract respectively
title_list = []
author_list = []
abstract_list = []
reg3 = re.compile(r'Authored\sby:([\s\S]*?)Abstract')
reg4 = re.compile(r'([\s\S]+?)Authored\sby')
reg5 = re.compile(r'Abstract([\s\S]+?)1\sPaper\sBody')
tokenizer = RegexpTokenizer(r'[A-Za-z]\w+(?:[-?]\w+)?')
for key, value in files.items():
    if reg4.search(value):
        title_list.append(reg4.search(value).group(1))
    if reg3.search(value):
        author_list.append(reg3.search(value).group(1))
    if reg5.search(value):
        abstract_list.append(reg5.search(value).group(1))   
author = get_author(author_list)
title = get_title(title_list)
abstract = get_abstract(abstract_list)
combine_list = list(zip(title, abstract, author)) 

In [220]:
df = pd.DataFrame(combine_list, columns= ['top10_terms_in_abstracts','top10_terms_in_titles','top10_authors'])
df.to_csv('Group148_stats.csv', index=False)

PermissionError: [Errno 13] Permission denied: 'Group148_stats.csv'

In [221]:
def get_author(value):
    author_list = ''.join(value)
    author_list = author_list.splitlines()
    author_list = [x for x in author_list if x] 
    author_list = FreqDist(author_list).most_common(10)
    author_list = sorted(author_list, key = lambda x: (-x[1], x[0]))
    author_list = [x[0] for x in author_list]
    return author_list

In [222]:
def get_title(value):
    title_list = [x.strip() for x in value]
    title_list = ''.join(title_list)
    title_list = re.sub(r'\n',' ',title_list)
    tokenizer = RegexpTokenizer(r'[A-Za-z]\w+(?:[-?]\w+)?')
    title_list = tokenizer.tokenize(title_list)
    title_list = [x.lower() for x in title_list]
    title_list = [x for x in title_list if x not in stop_word]
    title_list = FreqDist(title_list).most_common(10)
    title_list = [x[0] for x in title_list]
    return title_list    

In [212]:
def get_abstract(value):
    abstract_list = [x.strip() for x in value]
    abstract_list = ''.join(abstract_list)
    abstract_list = re.sub(r'\n',' ',abstract_list)
    abstract_list = re.sub(r'\-\s','',abstract_list)
    abstract_list = sent_tokenize(abstract_list)
    abstract_list = [x[0].lower() + x[1:] for x in abstract_list]
    abstract_list = ''.join(abstract_list)
    tokenizer = RegexpTokenizer(r'[A-Za-z]\w+(?:[-?]\w+)?')
    abstract_list = tokenizer.tokenize(abstract_list)  
    abstract_list = [x for x in abstract_list if x not in stop_word]
    abstract_list = FreqDist(abstract_list).most_common(10)
    abstract_list = [x[0] for x in abstract_list]
    return abstract_list

In [126]:
# fd_3 = FreqDist(abstract_list)
# fd_3.most_common(10)

In [125]:
# fd_1 = FreqDist(author_list)
# fd_1.most_common(10)

In [124]:
# fd_2 = FreqDist(title_list)
# fd_2.most_common(10)

In [186]:
# def choose(item):
#     return [i[0] for i in item]

In [185]:
# abstract = choose(sort_abstract)
# title = choose(sort_title)
# author = choose(sort_author)
# abstract
# title
# author

In [184]:
# list_d =zip(abstract, title, author)
# list2 = list(list_d)

In [183]:
# df = pd.DataFrame(list(zip(*[abstract, title, author])), columns= ['top10_terms_in_abstracts','top10_terms_in_titles','top10_authors'])
# df.to_csv('Group148_stats.csv', index=False)

In [123]:
# fd_1 = FreqDist(author)
# sort_author = fd_1.most_common(10)
# s = sorted(sort_author, key = lambda x: (-x[1], x[0]))
# fd_2 = FreqDist(title)
# sort_title = fd_2.most_common(10)
# fd_3 = FreqDist(abstract)
# sort_abstract = fd_3.most_common(10)

# list = choose(sort_abstract)
# list
# sort_abstract

In [127]:
# data_row=[grant_id,p_title,kind,number_of_claims,inventors_str,applicant_count,examiner_count,claims_text,abstract]
# data.append(data_row)
# #insert the list of data into dataframe 
# df=pd.DataFrame(data,columns=["grant_id","patent_kind","kind",'number_of_claims',"inventors",'citations_applicant_count',"citations_examiner_count","claims_text","abstract"])
# #convert dataframe into .csv file
# df.to_csv("Group148.csv",index=False)

In [122]:
# author_list = []
# reg3 = re.compile(r'Authored\sby:([\s\S]*?)Abstract')
# for key, value in files.items():
#     if reg3.search(value):
#         author_list.append(reg3.search(value).group(1))
# author_list = ''.join(author_list)
# author_list = author_list.splitlines()
# author_list = [each for each in author_list if each] 
# # #         author = [clean(each) for each in author_list]
# #         author_list = [each.strip() for each in author_list]
# #         author = [each.splitlines() for each in author_list]
# #         author = [each for sublist in author for each in sublist]
# #         author = [each for each in author if each]        
# author_list

In [121]:
# fd_1 = FreqDist(author_name)
# sort_author = fd_1.most_common(10)
# sort_author

In [122]:
# fd_1 = FreqDist(author_name)
# sort_author = fd_1.most_common(10)
# # sort_author
# # [v[0] for v in sorted(fd_1.iteritems(), key=lambda k,v: -v,k )]
# # list = [v[0] for v in sorted(fd_1.items(), key=lambda k,v: v,k)]
# # # fd_1
# # list
# s = sorted(sort_author, key = lambda x: (-x[1], x[0]))
# s

In [121]:
# title_list = []
# reg4 = re.compile(r'([\s\S]+?)Authored\sby')
# for key, value in files.items():
#     if reg4.search(value):
#         title_list.append(reg4.search(value).group(1))
# title_list = clean(title_list)
# title_list = tokenizer(title_list)
# title_list = [token.lower() for token in title_list]
# title_list = [w for w in title_list if w not in stop_word]
# # title_list = [each for each in title_list if each] 
# #         title_list = [clean(each) for each in title_list]
# # #         title_list = [each.strip() for each in title_list]
# # #         title_list = [re.sub(r'\n',' ',each) for each in title_list]
# #         tokenizer = RegexpTokenizer(r'[A-Za-z]\w+(?:[-?]\w+)?')
# #         title = [tokenizer.tokenize(each) for each in title_list]~
# #         title = [tokenizer(each) for each in title_list]
# #         title = [item for sublist in title for item in sublist]
# #         title = [token.lower() for token in title]
# #         title = [w for w in title if w not in stop_word]
# title_list

In [120]:
# fd_2 = FreqDist(title_list)
# fd_2.most_common(10)

abstract

In [119]:
# abstract_list = []
# reg5 = re.compile(r'Abstract([\s\S]+?)1\sPaper\sBody')
# for key, value in files.items():
#     if reg5.search(value):
#         abstract_list.append(reg5.search(value).group(1))
# abstract_list = clean(abstract_list)
# abstract_list = sent_token(abstract_list)
# abstract_list = tokenizer(abstract_list)
# abstract_list = [w for w in abstract_list if w not in stop_word]
# #         abstract_list = [clean(each) for each in abstract_list]
# #         abstract = [sent_tokenize(each) for each in abstract_list]
# #         abstract = [item for sublist in abstract for item in sublist]
# #         abstract = [each[0].lower() + each[1:] for each in abstract]
# #         tokenizer = RegexpTokenizer(r'[A-Za-z]\w+(?:[-?]\w+)?')
# #         abstract = [tokenizer.tokenize(each) for each in abstract]
# #         abstract = [item for sublist in abstract for item in sublist]
# #         abstract = [w for w in abstract if w not in stop_word]
# # abstract_list
# abstract_list

In [118]:
# fd_3 = FreqDist(abstract_list)
# fd_3.most_common(10)